# Chapter 4: Statistical Data Analysis II - Parameter Estimation (Part 3)

## Parameter uncertainties

In parameter estimation, a distinction is made between point estimation and interval estimation. The **point estimate** only provides an estimator $\hat{\mathbf{a}}$ for the parameters of the model function. In addition, however, an uncertainty interval for the parameter is of interest, as a confidence interval constructed from data, so that in the sense of frequentist statistics a certain proportion (e.g., 68.3%) of all intervals contain the true value. This procedure is called **interval estimation**. This interval could be two-sided (casually formulated: "Parameter is between...") or one-sided ("Parameter is less than" or "Parameter is greater than"). In modern mathematical statistics, maximum likelihood methods are almost always used for this purpose; however, these go beyond the scope of this course and are only briefly discussed in the outlook. In this chapter, we will limit ourselves to determining the variance of the estimator within the least squares method (LS method, also known as the $\chi^2$ method).

### Variance of the estimator illustrated
Using the analytically solvable example of a repeated measurement of an observable, we want to establish a relationship between the variance of the estimator for this observable and the residual sum of squares $S$. We assume that we carry out $N$ measurements $y_i$ of a constant observable with the true value $a=3$, i.e., $\lambda_i \equiv \lambda = a$. The variance is the same in each of these measurements: $\sigma_i \equiv\sigma=1$. Using the method of least squares, we estimate the parameter by minimizing $S$:
$$
S\equiv\chi^2=\sum_i \frac{(y_i-a)^2}{\sigma^2} \overset{!}{=} \mathsf{min}
$$
In the first part of this chapter you will find a code example with an animation in which possible values of $a$ are inserted into this equation and the value of $S$ is plotted against $a$ in each case. The question of how precisely the estimator $\hat{a}$ is known is answered by determining its variance $\mathsf{V}[\hat{a}]$. It is instructive to look at $S(a)$ for an estimate from more and more data points. Using linear error propagation (auxiliary calculation follows), we expect the variance $\mathsf{V}[\hat{a}]$ to shrink by a factor of $1/N$ with $N$ measurements (and thus the standard deviation by $1/\sqrt{N}$), i.e.,
$$
\mathsf{V}[\hat{a}] = \frac{\sigma^2}{N}.
$$

>**Auxiliary calculation**: The variance of $\hat{a}$ can be calculated using the linear law of uncertainty propagation. As a constant is a linear model function, the result is exact:
>$$
\mathsf{V}[\hat a] = \sum_j \left( \frac{\partial \hat a}{\partial y_j}\right)^2 \cdot \sigma_j^2.
>$$
>With $\hat{a}$ and the partial derivative of $\hat{a}$ with respect to the $y_i$
>$$
\hat a = \frac{1}{\sum_i 1/\sigma_i^2} \sum_i \frac{y_i}{\sigma_i^2}, \quad
\frac{\partial \hat a}{\partial y_j} = \frac{1}{\sum_i 1/\sigma_i^2} \frac{1}{\sigma_j^2}
>$$
>gives the variance of $\hat{a}$
>$$
\mathsf{V}[\hat a] = \frac{1}{(\sum_i 1/\sigma_i^2)^2} \sum_j \frac{\sigma_j^2}{\sigma_j^4} = \frac{1}{\sum_i 1/\sigma_i^2}\overset{\sigma_i \equiv \sigma}{=} \frac{\sigma^2}{N}.
>$$

This is implemented in the following code example:

In [ ]:
"""least squares: residual sum of squares adding more and more data"""

import numpy as np
import matplotlib.pyplot as plt

def LeastSquares_S( model, sigma, data ):
	"""least squares: function to compute residual sum of squares"""

	# use np.meshgrid to process arrays of models applied on the same data
	MODEL, DATA = np.meshgrid( model, data )
	return np.sum( ( ( DATA - MODEL ) / sigma )**2, axis=0 )

# true model parameters
atrue = 3
sig   = 1

# scan of a values
amin, amax, steps = 0., 6., 300
a = np.linspace( amin, amax, steps )

# data points
N = 5
xi = np.linspace( 1, N, N )
xrange = np.linspace( 0.5, N + 0.5, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=N )

fig,ax = plt.subplots( 2, N, figsize=(25,10) )

for i in np.arange( len( yi ) ):

	# compute S(a) with first i+1 data points
	S_plot = LeastSquares_S( a, sig, yi[:i+1] )
	
	# plot data points
	ax[0][i].errorbar( xi[:i+1], yi[:i+1], yerr=sig, fmt="ro" )
	ax[0][i].set_xlabel( r"$x$")
	ax[0][i].set_ylabel( r"$y$")
	ax[0][i].set_xlim( 0, 6 )
	ax[0][i].set_ylim( 0, 6 )
	ymean = np.repeat( np.mean( yi[:i+1] ), steps )
	ax[0][i].plot( xrange, ymean, "r--" )

	# plot S(a)
	ax[1][i].plot( a, S_plot )
	ax[1][i].set_xlabel( r"$a$")
	ax[1][i].set_ylabel( r"$S(a)$")
	ax[1][i].set_xlim( 0, 6 )
	ax[1][i].set_ylim( 0, 50 )
	ax[1][i].text( 0.5, 45, "$N=%d$" % (i+1) )

plt.show()

As can be seen in the output of the code example, the parabola becomes narrower and steeper with more data points. The curvature of the parabola in the value range around the minimum could be a suitable measure of the uncertainty on $\hat{a}$. Mathematically, this curvature corresponds to the second derivative of $S$ with respect to the parameter $a$:
$$
\begin{split}
S &= \sum_i \frac{(y_i-a)^2}{\sigma^2} \overset{!}{=} \mathsf{min},\\
\frac{\partial S}{\partial a} &= -2\sum_i\frac{y_i-a}{\sigma^2},\\
\frac{\partial^2 S}{\partial a^2} &= 2\sum_i\frac{1}{\sigma^2} = \frac{2N}{\sigma^2}.
\end{split}
$$
In the case of more than one parameter, i.e., $\mathbf{a}=(a_i,\dots,a_m)$, the second derivative is replaced by the matrix of the second partial derivatives (Hessian matrix).

The comparison with the expectation from above shows that, initially for this special case, the reciprocal of the variance corresponds to the second derivative of $S$ after the parameter, i.e. the curvature of $S$, up to a factor of 1/2:
$$
\frac{1}{2}\frac{\partial^2 S}{\partial a^2} = \frac{N}{\sigma^2}=
\frac{1}{\mathsf{V}[\hat{a}]} \equiv \mathsf{V}[\hat{a}]^{-1}.
$$

This relationship between the curvature of $S$ and the covariance matrix can also be shown in general for the linear LS method. The most general form of $S$ for a model function linear in the parameters ($\boldsymbol{\lambda}=\mathbf{Aa}$) is
$$
S\equiv\chi^2\equiv
(\mathbf{y} - \mathbf{A}\mathbf{a})^\mathsf{T}\,
\mathbf{V}^{-1}\,
(\mathbf{y} - \mathbf{A}\mathbf{a}) \overset{!}=\mathsf{min}
$$
The gradient of $S$ with respect to the parameters $\mathbf{a}$ then results as
$$
\vec{\nabla}_\mathbf{a} S =
-2\, \mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{y} +
2\, \mathbf{A}^\mathsf{T}\,\mathbf{V}^{-1}\,\mathbf{A}\,\mathbf{a}
$$
and the matrix of second partial derivatives at the minimum $\hat{\mathbf{a}}:$
$$
\left.
\frac{1}{2}\frac{\partial^2 S}{\partial a_i \, \partial a_j}\right|_\mathbf{\hat{a}} =
(\mathbf{A}^\mathsf{T}\,
\mathbf{V}^{-1}\,
\mathbf{A})_{ij}.
$$
A comparison with the analytical calculation of the covariance matrix at the beginning of chapter 4,
$$
\mathbf{V}[\hat{\mathbf{a}}] =
\mathbf{B}\mathbf{V}\mathbf{B}^\mathsf{T} =
(\mathbf{A}^\mathsf{T}\mathbf{V}^{-1}\mathbf{A})^{-1},
$$
shows that
$$
\left.\frac{1}{2}\frac{\partial^2 S}{\partial a_i \, \partial a_j}\right|_\mathbf{\hat{a}} =
(\mathbf{V}[\mathbf{\hat a}]^{-1})_{ij},
$$
so that the inverse of the covariance matrix corresponds to the Hessian matrix of $S$ (evaluated at the minimum: $\mathbf{a}=\hat{\mathbf{a}}$) up to a factor of 1/2.

### Variance: graphical method
The relationship between variance and curvature of $S$ at the minimum can also be established in a **graphical** way. We go back to the case of a single parameter $a$. The aim here is to read off the variance $\mathsf{V}[\hat{a}]$ or standard deviation $\sigma_{\hat{a}}$ directly from the graphical representation of $S(a)$. This is achieved by drawing a horizontal line in the graph whose intersection points with $S(a)$ form an interval around $\hat{a}$ that corresponds to $\sigma_{\hat{a}}$. The vertical distance of the horizontal line from the minimum is given by
$$
 \Delta \chi^2 \equiv \Delta S \equiv S(a) - S(\hat{a})
$$
For further discussion, we approximate $S(a)$ by a parabola obtained by a Taylor expansion around the minimum $\hat{a}$, which we truncate after the quadratic term:
$$
S(a) \approx S(\hat{a}) +
\left.\frac{\partial S(a}{\partial a}\right|_{\hat a_i} (a - \hat{a}) +
\frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2 =
S(\hat{a}) +
\frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2,
$$
where we have used in the second step that the first derivative vanishes at the minimum. This means that
$$
\Delta \chi^2 = \frac{1}{2} \left.\frac{\partial^2 S(a)}{\partial a^2}\right|_{\hat a} (a - \hat{a})^2
$$
and with the relationship between the second derivative at the minimum and the variance:
$$
\Delta \chi^2 = \frac{(a-\hat{a})^2}{\sigma_{\hat{a}}^2}.
$$
For $\Delta \chi^2=1$ we obtain:
$$
\sigma_{\hat{a}}^2 = (a-\hat{a})^2 \quad\to\quad
a = \hat{a} \pm \sigma_{\hat{a}}
$$
This is the graphical solution for the standard deviation:
>A horizontal line at a vertical distance of $\Delta \chi^2=1$ from the minimum intersects the function graph of $S(a)$ at a distance of $\pm \sigma_{\hat{a}}$ from the minimum $\hat{a}$.

The following code example illustrates this relationship:

In [ ]:
"""least squares: graphical solution for variance"""
import numpy as np
import matplotlib.pyplot as plt

# true model parameters
atrue = 3
sig   = 1

# data points
N = 5
xi = np.linspace( 1, N, N )

# scan of a values
amin, amax, steps = 2, 4, 200
a = np.linspace( amin, amax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=N )

# plot
fig,ax = plt.subplots()

# compared to the code example above, this is an alternative way to compute S using list comprehension
S_plot = np.array( [ np.sum( ( ( yi - a_plot ) / sig )**2 ) for a_plot in a ] )

# this is a way to compute the minimum of the curve and the interval
S_min = S_plot.min()    # minimal value of S
i_min = S_plot.argmin() # index of minimal value
i_sigma, = np.where( S_plot < S_min+1 ) # range of indices where S is below S_min+1, first and last index are +/- 1 sigma

ax.plot( a, S_plot )
ax.set_xlabel( r"$a$")
ax.set_ylabel( r"$S(a)$")
ax.set_xlim( amin, amax )
ax.set_ylim( 5, 12 )

ax.vlines( (a[i_min], a[i_sigma[0]], a[i_sigma[-1]]), 5, 10, linestyles="dashdot" )
ax.hlines( (S_min,S_min+1), amin, amax, linestyles="dashed" )

ax.text( 3.75, S_min+0.1, r"$\Delta \chi^2=0$" )
ax.text( 3.75, S_min+1.1, r"$\Delta \chi^2=1$" )
ax.text( a[i_min], 10.2, r"$\hat{a}$", ha="center")
ax.text( a[i_sigma[0]], 10.2, r"$\hat{a}-\sigma_{\hat{a}}$", ha="center")
ax.text( a[i_sigma[-1]], 10.2, r"$\hat{a}+\sigma_{\hat{a}}$", ha="center")

plt.show()

The above consideration also works for model functions that depend on more than one parameter and/or are non-linear in the parameters. In this case, the Taylor expansion is
$$
S(\mathbf{a}) \approx
S(\mathbf{\hat a}) +
\sum_i \left.\frac{\partial S(\mathbf{a})}{\partial a_i}\right|_{\hat a_i}
(a_i - \hat a_i) +
\sum_{i,j} \left.\frac{1}{2} \,\frac{\partial^2 S(\mathbf{a})}{\partial a_i \, \partial a_j}\right|_{\hat a_i, \hat a_j}
(a_i - \hat a_i)(a_j - \hat a_j)
$$
At the minimum $\mathbf{a}=\hat{\mathbf{a}}$ all first partial derivatives vanish and the matrix of the second partial derivatives (Hessian matrix) corresponds to the inverse covariance matrix $\mathbf{V}[\mathbf{\hat a}]^{-1}$.

>**Outlook**: The graphical method for estimating the variance works not only for the LS method, but also for the more general maximum likelihood method.

>**Excursus: What is an uncertainty bar?**
>
>After the above considerations on estimating the variance, it is worth returning to the meaning of the uncertainty bar for describing uncertainties. The specification of estimated value and uncertainty $\hat{a} \pm \sigma_{\hat{a}}$ is roughly interpreted as an interval that "covers 68.3% probability". In frequentist statistics, the exact interpretation is: 68.3% of all intervals calculated from different samples $\hat{a} \pm \sigma_{\hat{a}}$ contain the true value $a$. In this view, the **uncertainty bar is assigned to the data point**.
>
>However, another view of uncertainty bars is also conceivable, in which the **uncertainty bar is assigned to the true value** (or the model function). In this view, the data point has no uncertainty ("the data is the data"). This view corresponds to our model of a measurement in which the true value is smeared by random contributions. This means that the estimated values $\hat{a}$ follow a certain probability distribution in the parameter space $f(\hat{a};a)$, e.g., a normal distribution. This distribution can be translated into a distribution $g(y_i;\lambda_i)$ of the measured values $y_i$ around the values of the model function $\lambda_i$ at the position $x_i$ by a variable transformation. This is also consistent with this view that the variance $\sigma_i^2$ or the covariance matrix $\mathbf{V}$, which is included in the LS method, is actually the variance of the true value and - if not known - must be estimated using the variance of the individual measurement.
>
>The following figure compares both views:
><img src="img/uncertainty_bar.png" width=80%>

### Variance: pseudo-experiments
In many cases, the variance can also be estimated using a method based on random numbers. The idea is to simulate the measurement and its uncertainties on the computer. For this reason, this method is often referred to as the method of **pseudo-experiments**, also known as "ensemble tests" or the "toy Monte Carlo" method. We assume that the values of model function at the measurement positions correspond to the true values and that the probability distribution of the uncertainties is known. This approach is similar to our model of a measurement, in which measurements are simulated on a computer by adding a random contribution from a known probability distribution (e.g. normal distribution) to the true value: $m=w+z$ The difference is that the true value is not known for the pseudo-experiments, but is replaced by the measured value from the real measurement. This lack of knowledge is irrelevant for estimating the variance.

The advantage of variance estimation using pseudo-experiments is that it is **exact** (with known probability distributions) and can often be **implemented with little effort**. A disadvantage is the relatively high computational cost - it is to a certain extent a "brute force" method, see also the excursus on sustainability in computing below. Uncertainty propagation can also be implemented precisely and easily with pseudo-experiments, see the example on the uncertainty of the ratio of two random variables in Chapter 2.

In the following code example, the uncertainty of a fit is to be determined using pseudo-experiments. A straight line is fitted to ten measured values with uncertainties in $x$ and $y$. We are looking for the uncertainties on the slope and $y$-intercept and their (anti-)correlation with known normally distributed uncertainties of the measured values. From the ten real measured values, we now draw a new pseudo-experiment 1000 times, each with ten simulated measured values. For each simulated measured value, the real measured value is taken as the true value and shifted by a random contribution in $x$ and $y$. Then an adjustment is performed with `kafe2.xy_fit()` and the parameter values are histogrammed. Only the fitted values from the pseudo-experiments are used, but not the uncertainties from the fits. Nevertheless, the uncertainties of the slope and $y$-intercept can be determined from the standard deviation of the histograms and the correlation of these parameters from the correlation coefficient of the scatter plot. The mean values of the histograms, by construction, correspond to the real measured values that were inserted into the pseudo-experiments.

In [ ]:
"""Using kafe2 for a straight line fit in the laboratory course
uncertainties determined from pseudoexperiments (or: toy MC)"""

import numpy as np
import matplotlib.pyplot as plt
from PhyPraKit import generateXYdata 
from kafe2 import xy_fit, plot

# range of values
n, xmin, xmax = 10, 1., 10.
xdata = np.linspace( xmin, xmax, n )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight line)'''
	return a0 + a1*x
	
# true parameter values	
lin_modell_pars = [ 1.0, 0.3 ]

# absolute uncertainty for x value, relative uncertainty for y
ey_rel = 0.1
ex = 0.3

# generate synthetic data according to linear model
xtrue, ytrue, ydata = generateXYdata( xdata, lin_model, ex, 0., srely=ey_rel, mpar=lin_modell_pars )
ey = ey_rel * ytrue 

# generate Npe pseudoexperiments
rng = np.random.default_rng( 42 )
Npe = 1000
par = np.zeros( (Npe, 2) )

for i in np.arange( Npe ):
	"""new pseudoexperiment: draw random x and y values from Gaussian distribution
	using mu = measured value and sigma = given uncertainty and fit these synthetic data points"""
	xpe = rng.normal( size=n, loc=xdata, scale=ex )
	ype = rng.normal( size=n, loc=ydata, scale=ey )
	result = xy_fit( lin_model, xpe, ype, x_error=ex, y_error=ey, save=False )
	par[i] = result['fit'].parameter_values

a0, a1 = par[:,0], par[:,1]
fig,ax = plt.subplots( 2, 2, figsize=(12,10) )

ax[0][0].hist( a0 )
ax[0][0].set_xlabel( r"$a_{0}$" )
ax[0][0].set_ylabel( "Frequency" )
ax[0][0].text(0.66, 0.85, r"$\hat{\mu} = $%5.3f %s$\hat\sigma = $%5.3f" % (np.mean( a0 ), "\n", np.std( a0, ddof=1 ) ), transform=ax[0][0].transAxes, backgroundcolor='white')

ax[1][1].hist( a1 )
ax[1][1].set_xlabel( r"$a_{1}$" )
ax[1][1].set_ylabel( "Frequency" )
ax[1][1].text(0.66, 0.85, r"$\hat{\mu} = $%5.3f %s$\hat\sigma = $%5.3f" % (np.mean( a1 ), "\n", np.std( a1, ddof=1 ) ), transform=ax[1][1].transAxes, backgroundcolor='white')

ax[1][0].scatter( a1, a0 )
ax[1][0].set_xlabel( r"$a_{1}$" )
ax[1][0].set_ylabel( r"$a_{0}$" )
ax[1][0].text(0.66, 0.85, r"$\hat{\rho} = $%5.3f" % np.corrcoef( a1, a0 )[1][0], transform=ax[1][0].transAxes, backgroundcolor='white')

xline = np.linspace( xmin-0.5, xmax+0.5, 200 )
result = xy_fit( lin_model, xtrue, ytrue, x_error=ex, y_error=ey, save=False )

# kafe2 fit returns parameter estimates
pardata = result['fit'].parameter_values
ax[0][1].errorbar( xdata, ydata, xerr=ex, yerr=ey, fmt='bo' )
ax[0][1].plot( xline, lin_model( xline, *pardata ), 'r--' )
ax[0][1].set_xlabel( r"$x$" )
ax[0][1].set_ylabel( r"$y$" )

# kafe2 fit also returns asymmetric uncertaintties and correlation matrix
parunc  = result['fit'].asymmetric_parameter_errors
parcorr = result['fit'].parameter_cor_mat
ax[1][0].text(0.60, 0.10, r"$a_0 = %5.3f^{+%5.3f}_{%5.3f}$%s$a_1 = %5.3f^{+%5.3f}_{%5.3f}$%s$\rho = %5.3f$" % (pardata[0],parunc[0][1],parunc[0][0],"\n",pardata[1],parunc[1][1],parunc[1][0],"\n",parcorr[1][0]), transform=ax[0][1].transAxes, backgroundcolor='white')

plt.show()

>**Excursus: Computing and sustainability**
>
>The computing power of modern computers has made methods such as pseudo-experiments (or machine learning) easily accessible. The 1000 pseudo-experiments took about 16 seconds on a laptop from the year 2022. Nevertheless, this effort to determine the uncertainty is much higher than that for a single fit to the data and an estimation of the covariance matrix from this fit. As in other areas of life, science should also pay attention to the consumption of resources - efficient computer code and resource-saving methods contribute to this endeavor.

### Correlated uncertainties
In one dimension, the interval $\pm1\sigma$ of the normal distribution is used as the basis for specifying the uncertainties of a random variable. In the graphical method, the residual sum of squares $S$ around the minimum was considered and the 1-$\sigma$ interval was constructed with the rule $\Delta S\equiv\Delta \chi^2=1$.

Random variables are generally **correlated** in more than one dimension. As shown above, such a correlation already occurs for the slope and intercept of a simple straight line.
Therefore, for more than one random variable, the complete covariance matrix should ideally be specified instead of the 1-$\sigma$ interval. Unfortunately, this is (too) often not the case in practice – correlations are even completely ignored.

To visualize the elements of the covariance matrix graphically, it is useful to represent the correlated uncertainties of pairs of random variables. Therefore, their functional form is given explicitly here. The role played in one dimension by the scaling parameter $\sigma$ of a univariate normal distribution is assumed in two dimensions by the matrix $\boldsymbol{\sigma}$ of the bivariate normal distribution (Chapter 2).
$$
\boldsymbol{\Sigma} =
\begin{pmatrix}
\sigma_1^2 & \rho_{12} \,\sigma_1\sigma_2 \\
\rho_{12} \,\sigma_1\sigma_2 & \sigma_2^2
\end{pmatrix}.
$$
In the normal distribution, the determinant of $\boldsymbol{\sigma}$,
$$
\det\boldsymbol{\sigma} = \sigma_1^2 \sigma_2^2 ( 1 - \rho_{12}^2),
$$
and its inverse,
$$
\boldsymbol{\sigma}^{-1} =
\frac{1}{\sigma_1^2 \sigma_2^2 (1-\rho_{12}^2)}
\begin{pmatrix}
\sigma_2^2 & -\rho_{12} \,\sigma_1\sigma_2 \\
-\rho_{12} \,\sigma_1\sigma_2 & \sigma_1^2
\end{pmatrix},
$$
are required. This results in a two-dimensional PDF:
$$
\begin{split}
&f(x_1, x_2; \mu_1, \mu_2, \sigma_1, \sigma_2, \rho_{12}) =
\frac{1}{2\pi} \cdot
\frac{1}{\sigma_1\sigma_2\sqrt{1-\rho_{12}^2}} \cdot\\
&\exp\left[
-\frac{1}{2(1-\rho_{12}^2)}
\left[
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)^2 +
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)^2
- 2\rho_{12}
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)
\right]
\right]
\end{split}.
$$
We are looking for the two-dimensional analog of the 1-$\sigma$ interval. We obtain this requiring that the exponent in the above equation is equal to one. This is fulfilled if
$$
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)^2 +
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)^2
- 2\rho_{12}
\left(
\frac{x_1 - \mu_1}{\sigma_1}
\right)
\left(
\frac{x_2 - \mu_2}{\sigma_2}
\right)
= 2(1-\rho_{12}^2).
$$

This is the equation of an inclined ellipse, which is called **covariance ellipse** and is shown schematically here (image source: Glen Cowan, [Particle Data Group 2023](https://pdg.lbl.gov/2023/reviews/rpp2023-rev-statistics.pdf))

<img src="img/covariance_ellipse.png" width=50%>

The angle of inclination of the large major axis of this ellipse relative to the $x_1$-axis is
$$
\tan 2\phi =
\frac{2\rho_{12}\,\sigma_1\sigma_2}
{\sigma_2^2 - \sigma_1^2}.
$$
For more than two random variables, covariance ellipses are formed for each pair of variables. The area within the covariance ellipse then corresponds to a probability of 39.3% (and not 68.3%, see exkursus below). Hint: whenever you encounter a covariance ellipse, please check whether it is a two-dimensional $1\sigma$ interval or a two-dimensional 68.3% interval.

>**Excursus: Probability in $n$ dimensions**
>
> Like the probability interval of $\pm1\sigma$ of the normal distribution in one dimension, the volume within the $n$-dimensional covariance ellipsoid can also be assigned to a probability in $n$ dimensions. The expression in the exponent of the PDF of the multivariate normal distribution $((\mathbf{x} - \boldsymbol{\mu})^\mathsf{T} \boldsymbol{\Sigma}^{-1} (\mathbf{x}- \boldsymbol{\mu}))^{1/2} $ is also known as the Mahalanobis distance. It can be shown that for normal distribution in $n$ dimensions, the probability within a Mahalanobis distance of $t\sigma$ is given by a $\chi^2$ distribution with $n$ degrees of freedom. For $n=2$ then $\chi^2(t;2) = 1 - \exp[-t^2/2]$, i.e. $P=0.393$ for $t=1$ and $P=0.865$ for $t=2$.

The following code example the package [`kafe2`](https://kafe2.readthedocs.io/en/latest/) is used to show the  covariance ellipse for a non-linear least squares fit.

In [ ]:
"""demonstration of covariance ellipse for an LS fit in kafe2
based on an example from the kafe2 Beginners' Guide"""

#magic command needed to display plots inline
%matplotlib ipympl

import numpy as np
from kafe2 import xy_fit, plot, ContoursProfiler

def exponential_model(x, A_0=1., x_0=5.):
    """exponential function to model the data"""
    return A_0 * np.exp(x/x_0)

# data points with fixed absolute x uncertainty and relative y uncertainty
x_data = np.array( [0.38, 0.83, 1.96, 2.82, 4.28, 4.69, 5.97, 7.60, 7.62, 8.81, 9.87, 10.91] )
y_data = np.array( [1.60, 1.66, 2.12, 3.05, 3.57, 4.65, 6.21, 7.57, 8.27, 10.79, 14.27, 18.48] )
x_error = 0.3
y_error_rel = 0.02 * y_data

# Call kafe2 to fit data to exponential model (profile=True gives the error ellipse)
result=xy_fit( exponential_model, x_data, y_data, x_error=x_error, y_error_rel=y_error_rel, profile=True, save=False )
pl = plot( x_label="$x$", y_label="$A$", save=False )

# Call profile plot explicitly (otherwise the plot would not show inline)
# (in standalone scripts plot(plot_profile=True) would be sufficient)
cpl = ContoursProfiler( result['fit'] )
cpl.plot_profiles_contours_matrix()

### Least squares with uncertainties in $x$ and $y$
In physics, unlike some other scientific disciplines, **measured values are provided with uncertainties** wherever possible. Within the least squares method, the $y_i$ have uncertainties, but we have so far always assumed the positions $x_i$ to be **exactly known**. With a model function that is linear in the parameters, this resulted in the linear least squares (LS) method, for which there is an analytical solution.

However, it is much more realistic to assume - even in the physics laboratory course - that the $x_i$ also have uncertainties. The uncertainties of the $x_i$ and the $y_i$ may even be correlated. This requires an extension of the LS method, which makes the equations non-linear, so that a numerical solution is required. With modern computers and minimization algorithms, this is not an obstacle in practice. In standard programs for fitting functions to data, however, this functionality is often not available at all, as in the case of `scipy.optimize.curve_fit()`, or well hidden in submenus. The package [`kafe2`](https://kafe2.readthedocs.io/en/latest/) presented above, or fitting functions from [`PhyPraKit`](https://etpwww.etp.kit.edu/~quast/PhyPraKit/htmldoc/), which make use of `kafe2` internally, fill this "gap in the market" for the physics laboratory course and beyond. Data analysis software packages such as [`ROOT`](https://root.cern.ch) developed at CERN also provide this functionality.

The basic idea of correctly treating uncertainties in $x_i$ and $y_i$ is to add the uncertainties in $x_i$ (quadratically) to the uncertainties in $y_i$ and thus increase the "effective variance" of $y_i$. Geometrically, this corresponds to the determination of the two-dimensional distance $d$ of the data point from the model function, measured in the direction of the normal, perpendicular to the curve, and normalized to the uncertainties of $x_i$ and $y_i$. This is shown in the following figure:

<img src="img/xy_uncertainty.png" width=30%>

In practice, this task requires an iterative solution. We first consider the case in which the uncertainties $\sigma_{x_i}$ of the $x_i$ and $\sigma_{y_i}$ of the $y_i$ are uncorrelated. The sketch shows the distance of the data point from the curve:
$$
d = (y_i - \lambda(x_i;\mathbf{a})) \cos\alpha.
$$
The angle $\alpha$ can now be determined using the slope of the tangent to the model function:
$$
\frac{\partial \lambda(x;\mathbf{a})}{\partial x} \equiv \lambda^\prime = \tan\alpha.
$$
This means that the residual sum of squares, which must be minimized in the LS method, must be extended to
$$
S_e = \sum_{i=1}^{n}
\frac{(y_i - \lambda(x_i;\mathbf{a}))^2\, \cos^2\alpha}
{\sigma_{y_i}^2 \cos^2 \alpha + \sigma_{x_i}^2 \sin^2 \alpha}
= \sum_{i=1}^{n}
\frac{(y_i - \lambda(x_i;\mathbf{a}))^2}
{\sigma_{y_i}^2 + \sigma_{x_i}^2 \cdot(\lambda^\prime)^2},
$$
with $\sin^2 \alpha/\cos^2 \alpha = \tan^2 \alpha = \lambda^\prime$. A comparison with the original residual sum of squares shows that the variance in the denominator of the original expression has been replaced by
$$
{\sigma_{y_i}^2 + \sigma_{x_i}^2 \cdot(\lambda^\prime)^2}.
$$
The variance in $x$ is added quadratically to the variance in $y$, increasing the effective variance of $y_i$. The variance in $x$ is weighted by the square of the slope $\lambda^\prime$: the steeper the model function is at the position $x_i$, the greater the influence of the uncertainty of $x_i$ on the effective variance of $y_i$.

The $x$ value for which the distance is perpendicular to the model curve must now be determined iteratively. The algorithm for this consists of the following steps:
1. First, a fit is performed using the known least squares method without uncertainties in $x_i$ and a first estimate for the parameters $\hat{\mathbf{a}}$ is obtained.
1. A first value for the slope $\lambda^\prime$ is obtained by inserting $\hat{\mathbf{a}}$.
1. This value for the slope is used to minimize the (extended) residual sum of squares and a new estimate $\hat{\mathbf{a}}$ is obtained.
1. This value for $\hat{\mathbf{a}}$ is used to determine a new slope $\lambda^\prime$ and the previous step is repeated.

The iteration should be terminated when the estimated parameter values no longer change significantly - this is usually achieved after three to four iterations.

In the general case, we can proceed analogously. The expanded residual sum of squares is then given by
$$
S_e = \sum\limits_{i,j=1}^n
(y_i - \lambda(x_i; \mathbf{a} ))\,
(V^{-1})_{ij}\,
(y_j - \lambda(x_j; \mathbf{a} )).
$$
The $ij$ element of the covariance matrix of the uncertainties is the sum of the elements of the covariance matrices for the uncertainties in $y$ and $x$, where the $x$ uncertainty is weighted by the product of the slopes of the curve at the points $x_i$ and $x_j$:
$$
V_{ij} = V^y_{ij} + V^x_{ij} \cdot \lambda^\prime(x_i) \cdot \lambda^\prime(x_j).
$$

The following code example shows the application of the function `kafe2.xy_fit()` to simulated data (generated with the function `PhyPraKit.generateXYdata()`) with correlated uncertainties in $x$ and $y$. The comparison shows that by taking the $x$ uncertainty into account, the parameter uncertainties increase slightly and the $\chi^2$ probability increases accordingly.

>**Note** In this (and the previous) example, you can also see **asymmetric** uncertainties for the first time, i.e., the uncertainty intervals for values greater and smaller than the estimated value are different. This situation only occurs with the LS method in the non-linear case. In the maximum likelihood method, asymmetric uncertainties occur more frequently. In the graphical method of variance determination, this corresponds to the case in which $S(a)$ is not exactly parabolic. It can be shown that even in this case, the intersection points of $\Delta S=1$ with $S(a)$ determine the - then asymmetric - uncertainty interval.

In [ ]:
"""Using kafe2 for a straight line fit in the laboratory course: dealing with x and y uncertainties"""

#magic command needed to display plots inline
%matplotlib ipympl

import numpy as np
import matplotlib.pyplot as plt 
from PhyPraKit import generateXYdata
from kafe2 import xy_fit, plot

# range of values
n, xmin, xmax = 10, 1., 10.
xdata = np.linspace( xmin, xmax, n )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight line)'''
	return a0 + a1*x

# true parameter values
lin_model_pars  = [ 1.0, 0.3 ]

# absolute uncertainty on x values, relative uncertainty on y
ey_rel = 0.1
ex = 0.3

# correlated uncertainties in both x and y
xcorr, ycorr = 0.1, 0.3

# generate synthetic data according to linear model
xtrue, ytrue, ydata = generateXYdata( xdata, lin_model, ex, 0., srely=ey_rel, mpar=lin_model_pars, xrelcor=xcorr, yrelcor=ycorr )
ey = ey_rel * ytrue 

# straight line fit with kafe
result = xy_fit( lin_model, xdata, ydata, x_error=0, y_error=ey, save=False )
plot( x_label="x", y_label="y", save=False )
print( "Linear fit with y uncertainties only")
print( "Parameters:    ", result['fit'].parameter_values )
print( "Uncertainties: ", result['fit'].parameter_errors )
print( "Correlation matrix:\n", result['fit'].parameter_cov_mat )
print( "chi2, ndof, chi2/ndof: ", result['goodness_of_fit'], result['ndf'], result['gof/ndf'] )

# straight line fit with kafe
result = xy_fit( lin_model, xdata, ydata, x_error=ex, y_error=ey, save=False )
plot( x_label="x", y_label="y", save=False )
print( "Linear fit with x and y uncertainties")
print( "Parameters:    ", result['fit'].parameter_values )
print( "Uncertainties: ", result['fit'].parameter_errors )
print( "Correlation matrix:\n", result['fit'].parameter_cov_mat )
print( "chi2, ndof, chi2/ndof: ", result['goodness_of_fit'], result['ndf'], result['gof/ndf'] )

### Parameter-dependent uncertainties
The least squares method expects the variance $\sigma_i^2$ of the true value, i.e., the value of the model function $\lambda_i$. However, this is often not known and must be estimated from data on the sample variance $\hat{\sigma}^2$. If uncertainties are specified in absolute values, this difference is often negligible. However, if **relative** uncertainties are used, the difference can lead to a significant **bias** of the result. Examples of relative uncertainties are
- Relative uncertainty on the precision of a measuring device, e.g. 1%: $\sigma_i \to \hat{\sigma}_i=0.01 y_i$
- Counting experiments with Poisson uncertainties: $\sigma_i \to \hat{\sigma}_i = \sqrt{y_i}$

In both cases, the bias arises because the uncertainties are underestimated for $y_i < \lambda_i$, that is for a random deviation of the measurement data to smaller values ("downward fluctuation"), and at the same time the uncertainties are overestimated for $y_i > \lambda_i$, i.e., a random deviation to larger values ("upward fluctuations"). The uncertainties enter the sum of squares in the denominator; therefore, when fitting the model function, values that are **systematically too small are given too much weight and values that are too large are given too little weight**. As a result, the adjustment is "pulled down" and thus distorted.

A possible remedy is an iterative approach:
1. Fit to the data with estimation of the variance via the sample invariance.
1. New adjustment to the data with variance from the last adjustment.

In the following code example, a straight line is fitted to synthetic data with a relative uncertainty of 30% to illustrate the bias and the iterative approach. One of the data points is manipulated: it is shifted downwards and therefore has a very small absolute uncertainty. In the next iteration, we do not use the measured values to determine the relative uncertainties. Instead we estimate the relative uncertainties of each measurement from an evaluation of the model function at the position of the measurements, $\lambda_i$, using the model parameters from the last fit. After five iterations, stable, unbiased estimated values are obtained for the parameters of the straight line.

In [ ]:
"""Example: dealing with parameter-dependent uncertainties in kafe2"""

#magic command needed to display plots inline
%matplotlib ipympl

import numpy as np
import matplotlib.pyplot as plt 
from PhyPraKit import generateXYdata
from kafe2 import xy_fit, plot

# range of values
n, xmin, xmax = 10, 1., 10.
xdata = np.linspace( xmin, xmax, n )

def lin_model( x, a0=1., a1=1. ):
	'''linear model (straight line)'''
	return a0 + a1*x

# true parameter values
lin_modell_pars = [ 1.0, 0.3 ]

# generate synthetic data according to linear model
xtrue, ytrue, ydata = generateXYdata( xdata, lin_model, 0., 0., srely=ey_rel, mpar=lin_modell_pars )

# manipulate one data point to exaggerate the effect
ydata[3]=0.5

# compute relative uncertainties on y values (assuming x values do not have uncertainties)
ey_rel = 0.3
ey = ey_rel * ydata


# now iterate (niter times, until uncertainty stabilizes), replacing y uncertainty by result from previous fit
niter = 5
for i in np.arange( niter ):
	result = xy_fit( lin_model, xdata, ydata, y_error=ey, save=False )
	plot( x_label="x", y_label="y", save=False )
	par = result['fit'].parameter_values
	ey = ey_rel * lin_model( xdata, *par )	
	print( par )
